In [1]:
from elasticsearch import Elasticsearch
from itertools import groupby
from matplotlib import pyplot as plt
from tqdm import tqdm_notebook as tqdm
from influxdb import DataFrameClient
import datetime
import time
import pickle
import os
import sys
import pandas as pd
from pathlib import Path
import numpy as np
np.set_printoptions(suppress=True)
pd.set_option('display.float_format', lambda x: '%.0f' % x) #避免科学技术法
%matplotlib inline

# 时间转换

In [2]:
# 或者 '2015-08-28 16:43:37' --> 1440751417.0
def string2timestamp(strValue): 
    try:     
        d = datetime.datetime.strptime(strValue, "%Y-%m-%d %H:%M:%S.%f") 
        t = d.timetuple() 
        timeStamp = int(time.mktime(t)) 
        timeStamp = float(str(timeStamp) + str("%06d" % d.microsecond))/1000000
        print (timeStamp) 
        return timeStamp 
    except ValueError as e: 
        print (e) 
        d = datetime.datetime.strptime(strValue, "%Y-%m-%d %H:%M") 
        t = d.timetuple() 
        timeStamp = int(time.mktime(t)) 
        timeStamp = float(str(timeStamp) + str("%06d" % d.microsecond))/1000000
        print (timeStamp) 
        return timeStamp 


In [8]:
# 1440751417.283 --> '2015-08-28 16:43:37.283' 
def timestamp2string(timeStamp): 
    try: 
        d = datetime.datetime.fromtimestamp(timeStamp) 
        str1 = d.strftime("%Y-%m-%d %H:%M:%S.%f") 
        return str1 
    except Exception as e: 
        print (e) 
        return '' 

In [10]:
timestamp2string(1567084440)

'2019-08-29 21:14:00.000000'

In [13]:
es_time_trans        =  10**6. #es的timestamp_millis查找比转换结果多3位
influxdb_time_trans = 10**9. #influxdb的timestamp查找比转换结果多9位
es_start         = string2timestamp('2019-8-29 18:40:00.000000') * es_time_trans
es_end          = string2timestamp('2019-8-29 18:43:00.000000') * es_time_trans
influxdb_start = int(string2timestamp('2019-08-29 21:10:00.000000') * influxdb_time_trans)  #influxdb是UTC时间,int避免科学技术
influxdb_end  = int(string2timestamp('2019-08-29 21:25:00.000000') * influxdb_time_trans)
error_start = string2timestamp('2019-09-02 18:40:00.000000') * es_time_trans
error_end = string2timestamp('2019-09-02 18:43:00.000000') * es_time_trans

error_name = 'ts-basic-service'

1567075200.0
1567075380.0
1567084200.0
1567085100.0
1567420800.0
1567420980.0


# 导入ES数据

In [2]:
def search_all(index, body):
    rsp = es.search(index=index, body=dict(**body, size=1000), scroll='1m',request_timeout=30)
    total = rsp['hits']['total']
    print(total)
    scroll_id = rsp['_scroll_id']
    scroll_size = total
    with tqdm(total=total) as pbar:
        rets = []
        while scroll_size > 0:
            _rsp = es.scroll(scroll_id=scroll_id, scroll='1m')
            scroll_id = _rsp['_scroll_id']
            scroll_size = len(_rsp['hits']['hits'])
            total -= scroll_size
            rets.extend(parse(_rsp['hits']['hits']))
            pbar.update(scroll_size)        
    return rets


def parse(response):
    try:
        return list(map(
            lambda x: {
                'trace_id': x['_source']['traceId'],
                'timestamp': x['_source']['timestamp'],
                'latency': x['_source']['duration'],
                'http_status': x['_source']['tags']['http.status_code'],
                'request_parent_id': x['_source']['parentId'] if 'parentId' in x['_source'] else 'None',
                'request_id': x['_source']['id'],
                'source': x['_source']['localEndpoint']['serviceName'],
                'http_name': x['_source']['name'],
                'target': x['_source']['name'].split('.')[0] + '.default'
            },
            response,
        ))
    except KeyError:
        print('error:', response)

        
def dump_index(index):
    path = './event_title.txt'
    rets = search_all(
            index=index, 
            body={
                  "query": {
                    "range": {
                      "timestamp": {
                        "gte": es_start,
                        "lte" : es_end
                      }
                    }
                  }
                },
        
    )
    dump_path(path,rets)
    return rets

def dump_path(path,data):
    with open(path, 'wb+') as f:
        pickle.dump(data, f)

def load_path(path):
    with open(path, 'rb') as f:
        return pickle.load(f)


In [6]:
load_path('./invo_basic_8_29.pkl')

[{'trace_id': '00084bf4e31a5a323e2b69e8e2368ec6',
  'timestamp': [1567084543767839.0, 1567084514228823.0, 1567084467728282.0],
  'latency': [12180.0, 5057.0, 6323.0],
  'http_status': [200.0, 200.0, 200.0],
  'cpu_use': [7.516692265484355, 13.488154165510721, 13.488154165510721],
  'mem_use_percent': [0.3616714477539063, 0.32275390625, 0.32275390625],
  'mem_use_amount': [904675328.0, 806551552.0, 806551552.0],
  'file_write_rate': [0.0, 0.0, 0.0],
  'file_read_rate': [0.0, 0.0, 0.0],
  'net_send_rate': [16767.496558054154,
   29167.369974103156,
   29167.369974103156],
  'net_recieve_rate': [10648.726480036716,
   18328.322482795626,
   18328.322482795626],
  'endtime': [1567084543780019.0, 1567084514233880.0, 1567084467734605.0],
  's_t': ['ts-order-service->ts-order-service',
   'ts-station-service->ts-station-service',
   'ts-order-service->ts-station-service'],
  'label': 0},
 {'trace_id': '00340510346cd70a0ccc9d66eeff4443',
  'timestamp': [1567084546041882.0],
  'latency': [2760.

In [43]:
es = Elasticsearch(host='192.168.115.84', port=9200)
requests_8_29 = dump_index("zipkin:span-2019-08-29")
data_8_29=load_path('./event_title.txt')

27507


In [44]:
df = pd.DataFrame(data_8_29, columns=['trace_id',
                                      'timestamp',
                                      'latency',
                                      'http_status',
                                      'request_parent_id',
                                      'request_id',
                                      'source',
                                      'http_name',
                                      'target'] )

df = df.drop(columns=['request_parent_id','request_id','http_name'])
df['source']=df['source'].apply(lambda x : ('.'+x).strip('default').strip('.'))
df['target']=df['target'].apply(lambda x : ('.'+x).strip('default').strip('.'))
df

trace_id         timestamp   latency  \
0      3e4c92af33630580eca1ec210550f66f  1567084433090689    399404   
1      6d1bb6ea8133577502127e3401bbec41  1567084434031048     10673   
2      6d1bb6ea8133577502127e3401bbec41  1567084434067402      4362   
3      6d1bb6ea8133577502127e3401bbec41  1567084434078578      3502   
4      6d1bb6ea8133577502127e3401bbec41  1567084429023205    430160   
5      e5509cc13e65c4f7dd466bd545db0467  1567084429814289      6089   
6      094ac42cc35dc46b5cdf8558894cb4ba  1567084428913277     11953   
7      e5509cc13e65c4f7dd466bd545db0467  1567084429792736     10030   
8      e5509cc13e65c4f7dd466bd545db0467  1567084429557669    195677   
9      e5509cc13e65c4f7dd466bd545db0467  1567084427654258     27955   
10     343de65de97b4b436a82a6e57e3a93a3  1567084428301201      2204   
11     bbea3df54a1ec90782c77c46d8647dc0  1567084428369629    256937   
12     9d077ea244a1781361d76c77475aa55d  1567084429038264     15178   
13     6d1bb6ea8133577502127e3401bbec41  1567084426683637      4499   
14     6d1bb6ea8133577502127e3401bbec41  1567084429480588    195710   
15     6d1bb6ea8133577502127e3401bbec41  1567084430283610      4776   
16     e5509cc13e65c4f7dd466bd545db0467  1567084432097302      5215   
17     e5509cc13e65c4f7dd466bd545db0467  1567084430511563     46517   
18     3e4c92af33630580eca1ec210550f66f  1567084431561219    897216   
19     3e4c92af33630580eca1ec210550f66f  1567084431588431    892524   
20     6d1bb6ea8133577502127e3401bbec41  1567084432481649      2933   
21     6d1bb6ea8133577502127e3401bbec41  1567084432308176      4468   
22     6d1bb6ea8133577502127e3401bbec41  1567084432303600     10705   
23     e5509cc13e65c4f7dd466bd545db0467  1567084432301593    293898   
24     e5509cc13e65c4f7dd466bd545db0467  1567084429590630    199451   
25     e5509cc13e65c4f7dd466bd545db0467  1567084430618457      5403   
26     e5509cc13e65c4f7dd466bd545db0467  1567084409405094  21224069   
27     6d1bb6ea8133577502127e3401bbec41  1567084432419497      3795   
28     3e4c92af33630580eca1ec210550f66f  1567084431590186      5110   
29     6d1bb6ea8133577502127e3401bbec41  1567084428457178    301374   
...                                 ...               ...       ...   
26477  9a28743132ad6e41a4f8da9e6f643041  1567084774886140      8380   
26478  93a4322ce34d8f6b78ce0de1e81c3e57  1567084777490775      2474   
26479  c6c656202b8e94e75308c1e1a79dae48  1567084777076339      4105   
26480  93a4322ce34d8f6b78ce0de1e81c3e57  1567084777457002      3340   
26481  93a4322ce34d8f6b78ce0de1e81c3e57  1567084777508327      3242   
26482  93a4322ce34d8f6b78ce0de1e81c3e57  1567084777656483      3224   
26483  93a4322ce34d8f6b78ce0de1e81c3e57  1567084777824558      4032   
26484  93a4322ce34d8f6b78ce0de1e81c3e57  1567084777842418      6655   
26485  93a4322ce34d8f6b78ce0de1e81c3e57  1567084777991909      9145   
26486  28e73311f061fb28ea88c8529ff428bb  1567084774770621     37557   
26487  93a4322ce34d8f6b78ce0de1e81c3e57  1567084777475511      6220   
26488  93a4322ce34d8f6b78ce0de1e81c3e57  1567084777483688      7402   
26489  93a4322ce34d8f6b78ce0de1e81c3e57  1567084777510080      8718   
26490  93a4322ce34d8f6b78ce0de1e81c3e57  1567084777479197      3720   
26491  93a4322ce34d8f6b78ce0de1e81c3e57  1567084777449771     37962   
26492  93a4322ce34d8f6b78ce0de1e81c3e57  1567084777499488      5279   
26493  93a4322ce34d8f6b78ce0de1e81c3e57  1567084777508590      5001   
26494  e38d7f6fde67406319c57c56dd3277f6  1567084779260038      2645   
26495  e38d7f6fde67406319c57c56dd3277f6  1567084779354425      4114   
26496  e38d7f6fde67406319c57c56dd3277f6  1567084779368137      4151   
26497  e38d7f6fde67406319c57c56dd3277f6  1567084780029359      3446   
26498  e38d7f6fde67406319c57c56dd3277f6  1567084780046210      4322   
26499  e38d7f6fde67406319c57c56dd3277f6  1567084780333345      4184   
26500  e38d7f6fde67406319c57c56dd3277f6  1567084780073225      4284   
26501  e38d7f6fde67406319c57c56dd3277f6  15670847801498

# 获取influxdb的数据

In [117]:
#> SELECT * FROM "h2o_feet" WHERE time >= '2015-08-17T23:48:00Z' AND time <= '2015-08-18T00:30:00Z'
#print('数据库中的名称'+str(client.get_list_database()))
#print('数据库中的表'+str(client.query('show measurements;')))

In [14]:
svc = 'metric.ts-basic-service'
client = DataFrameClient('192.168.115.31',34002,'root','','aiops_metric')
query = f'select * from "{svc}" where time >= {influxdb_start} and time<= {influxdb_end}'
result = dict(client.query(query,chunked=False))

In [16]:
result['metric.ts-basic-service']

CPU使用率  内存使用率      内存使用量  文件系统写入速率  文件系统读取速率  \
2019-08-29 13:10:00+00:00      13      0  815517696         0         0   
2019-08-29 13:11:00+00:00      10      0  815321088         0         0   
2019-08-29 13:12:00+00:00      11      0  815554560         0         0   
2019-08-29 13:13:00+00:00      12      0  816939008         0         0   
2019-08-29 13:14:00+00:00      57      0  817836032         0         0   
2019-08-29 13:15:00+00:00      86      0  818368512         0         0   
2019-08-29 13:16:00+00:00     103      0  818016256         0         0   
2019-08-29 13:17:00+00:00      57      0  816222208         0         0   
2019-08-29 13:18:00+00:00      11      0  815742976         0         0   
2019-08-29 13:19:00+00:00      12      0  814891008         0         0   
2019-08-29 13:20:00+00:00       8      0  815808512         0         0   
2019-08-29 13:21:00+00:00      15      0  816025600         0         0   
2019-08-29 13:22:00+00:00      11      0  816422912         0         0   
2019-08-29 13:23:00+00:00      16      0  815226880         0         0   
2019-08-29 13:24:00+00:00      13      0  815271936         0         0   
2019-08-29 13:25:00+00:00       8      0  816054272         0         0   

                           网络发送速率  网络接收速率  
2019-08-29 13:10:00+00:00   64503   20238  
2019-08-29 13:11:00+00:00   63687   20101  
2019-08-29 13:12:00+00:00   47682   14639  
2019-08-29 13:13:00+00:00   50237   19375  
2019-08-29 13:14:00+00:00   26268   14260  
2019-08-29 13:15:00+00:00   41503   11787  
2019-08-29 13:16:00+00:00   44635   13041  
2019-08-29 13:17:00+00:00   50130   15229  
2019-08-29 13:18:00+00:00   52740   16406  
2019-08-29 13:19:00+00:00   47283   20897  
2019-08-29 13:20:00+00:00   61858   19055  
2019-08-29 13:21:00+00:00   67622   21364  
2019-08-29 13:22:00+00:00   65163   20396  
2019-08-29 13:23:00+00:00   73860   23193  
2019-08-29 13:24:00+00:00   60360   18930  
2019-08-29 13:25:00+00:00   51555   15900

In [46]:
result['metric.ts-basic-service'].to_csv('cpu.csv')

In [47]:
def get_db(svc):
    client = DataFrameClient('192.168.115.31',34002,'root','','aiops_metric')#初始化
    query = f'select * from "{svc}" where time >= {influxdb_start} and time<= {influxdb_end}'#time>now()-1h;
    result = dict(client.query(query,chunked=False))
    result = result[svc].reset_index().rename(columns={'index':'timestamp'})
    result['timestamp'] = result.apply(lambda x : x['timestamp'].timestamp(),axis=1)
    result['service'] = svc
    return result


#因为容器数目不一致，需要转换名称
def dflist_2_dblist(df):
    db_list=[]
    df_list=list(set(df['target']))
    for i in df_list:
        db_list.append('metric.'+i)
    return db_list


#读取fluxdb所有需要的数据为一个大表
def all_db(df):
    db_list=dflist_2_dblist(df)
    df=get_db(db_list[0])
    for i in db_list[1:]:
        df = pd.concat((df, get_db(i)))
    df['service']=df['service'].apply(lambda x:(x+'.').strip('metric').strip('.'))
    df = df.fillna(0)
    #cpu使用率，service，timestamp，内存使用率，内存使用量，文件系统写入速率，文件系统读取速率，网络发送速率，网络接受速率
    df.columns = ['cpu_use', 'target', 'timestamp', 'mem_use_percent', 'mem_use_amount', 
                         'file_write_rate',  'file_read_rate', 'net_send_rate', 'net_recieve_rate']
    return df

In [48]:
db_data = all_db(df)
db_data

/usr/local/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:25: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



cpu_use                        target  timestamp  mem_use_percent  \
0         6              ts-price-service 1567084200                0   
1         5              ts-price-service 1567084260                0   
2         2              ts-price-service 1567084320                0   
3         4              ts-price-service 1567084380                0   
4         4              ts-price-service 1567084440                0   
5         3              ts-price-service 1567084500                0   
6         3              ts-price-service 1567084560                0   
7         3              ts-price-service 1567084620                0   
8         3              ts-price-service 1567084680                0   
9         4              ts-price-service 1567084740                0   
10        4              ts-price-service 1567084800                0   
0        11              ts-order-service 1567084200                0   
1        17              ts-order-service 1567084260                0   
2        14              ts-order-service 1567084320                0   
3         8              ts-order-service 1567084380                0   
4         9              ts-order-service 1567084440                0   
5         5              ts-order-service 1567084500                0   
6         4              ts-order-service 1567084560                0   
7         8              ts-order-service 1567084620                0   
8         9              ts-order-service 1567084680                0   
9         9              ts-order-service 1567084740                0   
10        9              ts-order-service 1567084800                0   
0         2         ts-route-plan-service 1567084200                0   
1         2         ts-route-plan-service 1567084260                0   
2         2         ts-route-plan-service 1567084320                0   
3         2         ts-route-plan-service 1567084380                0   
4         1         ts-route-plan-service 1567084440                0   
5         1         ts-route-plan-service 1567084500                0   
6         1         ts-route-plan-service 1567084560                0   
7         2         ts-route-plan-service 1567084620                0   
..      ...                           ...        ...              ...   
3         6               ts-food-service 1567084380                0   
4         4               ts-food-service 1567084440                0   
5         2               ts-food-service 1567084500                0   
6         3               ts-food-service 1567084560                0   
7         4               ts-food-service 1567084620                0   
8         3               ts-food-service 1567084680                0   
9         8               ts-food-service 1567084740                0   
10        6               ts-food-service 1567084800                0   
0        10  ts-verification-code-service 1567084200                0   
1         4  ts-verification-code-service 1567084260                0   
2         3  ts-verification-code-service 1567084320                0   
3         3  ts-verification-code-service 1567084380                0   
4         2  ts-verification-code-service 1567084440                0   
5         5  ts-verification-code-service 1567084500                0   
6         3  ts-verification-code-service 1567084560                0   
7         2  ts-verification-code-service 1567084620                0   
8         2  ts-verification-code-service 1567084680                0   
9         3  ts-verification-code-service 1567084740                0   
10        4  ts-verification-code-service 1567084800                0   
0        14             ts-travel-service 1567084200                0   
1        13             ts-travel-service 1567084260                0   
2        11             ts-travel-service 1567084320                0   
3        14             ts-travel-service 1567084380          

# 按target和ts整合es和db

In [50]:
def time_to_little(data):
    n = (data - es_start ) // 60000000  
    return es_start/1000000 + n * 60

def es_time_to_little(df):
    df['timestamp'] = df['timestamp'].apply(time_to_little)#利用字典取分段函数
    df = df[~df['source'].isin(['istio-ingressgateway'])]
    return df

def zhenghe(df,db_data):
    df1 = df.copy()
    es_z = es_time_to_little(df1)
    result = pd.merge(es_z, db_data, on=['timestamp','target'])
    result['timestamp'] = df['timestamp']
    return result

In [51]:
zh=zhenghe(df,db_data)
zh

trace_id         timestamp  latency  \
0      3e4c92af33630580eca1ec210550f66f  1567084433090689   399404   
1      6d1bb6ea8133577502127e3401bbec41  1567084434031048   430160   
2      3e4c92af33630580eca1ec210550f66f  1567084434067402   897216   
3      e5509cc13e65c4f7dd466bd545db0467  1567084434078578   293898   
4      e5509cc13e65c4f7dd466bd545db0467  1567084429023205   199451   
5      6d1bb6ea8133577502127e3401bbec41  1567084429814289   303742   
6      e5509cc13e65c4f7dd466bd545db0467  1567084428913277   200645   
7      e5509cc13e65c4f7dd466bd545db0467  1567084429792736  2204431   
8      094ac42cc35dc46b5cdf8558894cb4ba  1567084429557669  2455034   
9      89a7ff1bbd0281b4460d9e2e27e47838  1567084427654258  2787051   
10     b30643a599a3129c86d096a55dd62999  1567084428301201   600001   
11     c09fb3d2266171f464e8e6b13180cdc8  1567084428369629  1098085   
12     c09fb3d2266171f464e8e6b13180cdc8  1567084429038264   108230   
13     c09fb3d2266171f464e8e6b13180cdc8  1567084426683637   837835   
14     89a7ff1bbd0281b4460d9e2e27e47838  1567084429480588   162934   
15     efa82c8331b951f3432686b4815d59c9  1567084430283610   191154   
16     89a7ff1bbd0281b4460d9e2e27e47838  1567084432097302   209975   
17     89a7ff1bbd0281b4460d9e2e27e47838  1567084430511563   298584   
18     e5509cc13e65c4f7dd466bd545db0467  1567084431561219  5025607   
19     e5509cc13e65c4f7dd466bd545db0467  1567084431588431   431547   
20     6d1bb6ea8133577502127e3401bbec41  1567084432481649   896953   
21     e5509cc13e65c4f7dd466bd545db0467  1567084432308176   297848   
22     e5509cc13e65c4f7dd466bd545db0467  1567084432303600   101572   
23     8a05d004f45b4ad86510183a124a7c7e  1567084432301593   302226   
24     e5509cc13e65c4f7dd466bd545db0467  1567084429590630  1498160   
25     8a05d004f45b4ad86510183a124a7c7e  1567084430618457    99685   
26     e5509cc13e65c4f7dd466bd545db0467  1567084409405094   279823   
27     8a05d004f45b4ad86510183a124a7c7e  1567084432419497  1759285   
28     8a05d004f45b4ad86510183a124a7c7e  1567084431590186   661682   
29     8a05d004f45b4ad86510183a124a7c7e  1567084428457178   393967   
...                                 ...               ...      ...   
24657  d4c9ea471020483f7f3688ff5e956274  1567084651422007  3319951   
24658  da61782b65b245dd46ebd03256b47aed  1567084652131083  2673857   
24659  194c6f5bb7cf224797a32a28550007f6  1567084651585158  1187482   
24660  a7bad639e97dfc07365ef338de66812c  1567084652156958  2025220   
24661  703e282d01835c32552c29630185e899  1567084642411744    81868   
24662  078da055a2b33281aaf6ec7a296ab282  1567084643581283    70636   
24663  40fedab92fb2aa10f6cab97b52d4aad0  1567084644548759   670993   
24664  5562bd1bc4b8139d3123ed2b628ec9ac  1567084706619543   934437   
24665  d849c30ebfabfbbdd629f710d25288ac  1567084706606755   923244   
24666  4dc66e86c223bea22018561f07141665  1567084707186487  1246681   
24667  93a4322ce34d8f6b78ce0de1e81c3e57  1567084707641772  1212778   
24668  38873a898eba15f5eba86be1521442e8  1567084706608337  2427896   
24669  c593546a0bcd0adfe321471dab061ba9  1567084707143450  1446386   
24670  dbe6d974b613da1b0b7c34d6bae132ec  1567084706861915  1357769   
24671  c593546a0bcd0adfe321471dab061ba9  1567084705347857  1447484   
24672  c268dde598689f2a7456cbc3075e6d08  1567084702863534  1682478   
24673  a653598c587f67aae9f3a7a573849fd3  1567084707693360   131143   
24674  51fcf06cae683490352c521c4a2ae157  1567084707695506   514613   
24675  8a292b5e5fe880b9330f53cad109214f  1567084707694451  7147073   
24676  045de2f539a07b420421b7cff8fea945  1567084706219003  5133336   
24677  6ba8db894bad92fae1341f540088d82c  1567084706539193   289679   
24678  e0459c47e22e606556d5bdeda50a2ea6  1567084711225672    11496   
24679  f49ad411686b5f4a4a9886e91f153cb5  1567084711531917    20479   
24680  025673044ec7b2ead38b07638778f9f9  1567084711511971    22510   
24681  02e049481ab7b3e92b34df49b65d4e60  1567084711625487  2009507   
24682  8853d61237c66937448f3855f9c9ba65  

# 转换为invocation

In [52]:
#endtime排序
def trans_csv(df):
    df['endtime']=df['timestamp']+df['latency']
    grouped = df.groupby('trace_id').apply(lambda x: x.sort_values('endtime', ascending=False))
    grouped['s_t']=grouped['source'].str.cat(grouped['target'],sep='->')
    grouped=grouped.drop(columns=['target','source','trace_id'])
    grouped.fillna(0)
    grouped.to_csv('grouped.csv') 
    return grouped

#trace每一行都整合为list，然后去掉重复的行
def trans(df):
    for i in df.columns[1:]:
        df[i]=str(list(df[i]))
    df=df.drop_duplicates(['trace_id'])
    return df

#得到按traceid整合后的invocation列表，没有error label
def trans_last(zh):
    trans_csv(zh)
    df=pd.read_csv('grouped.csv').drop(columns='Unnamed: 1')
    df1 = df.groupby('trace_id').apply(trans).drop(columns='trace_id')
    df1.to_csv('grouped1.csv')
    df2 = pd.read_csv('grouped1.csv').drop(columns='Unnamed: 1')
    return df2

#添加error的label
def error_label(error, df):
    outfile = df [ ( df['target'] == error ) & ( df['timestamp'] > error_start ) & (df['timestamp'] < error_end ) ] 
    error_traceid_set = set(outfile['trace_id'])
    return error_traceid_set

def int2list(int1):
    a=int1.strip('[]')
    a=[float(i) for i in a.split(',')]
    return a

def str2list(str1):
    a=str1.strip('[]')
    a=[i for i in a.split(',')]
    return a

# 得到最终invo，es+指标+label，以字典格式保存在txt文件中
def dict_last(zh,path):
    dfn = trans_last(zh)
    error_traceid = error_label(error_name, df)
    dfn['label'] = dfn.trace_id.apply(lambda x: 1 if x in error_traceid else 0)
    for i in dfn.columns[1:-2]:
        dfn[i] = dfn[i].apply(int2list)
    dfn['s_t'] = dfn['s_t'].apply(eval)
    dictn = dfn.to_dict(orient='records')
    dump_path(path,dictn)
    invo_dict=load_path(path)
    return invo_dict

In [53]:
invo_8_29 = dict_last(zh,'./invo_basic.pkl')
invo_8_29

[{'trace_id': '00084bf4e31a5a323e2b69e8e2368ec6',
  'timestamp': [1567084437311682.0, 1567084424169171.0, 1567084380676402.0],
  'latency': [12180.0, 5057.0, 6323.0],
  'http_status': [200.0, 200.0, 200.0],
  'cpu_use': [7.516692265484355, 13.488154165510721, 13.488154165510721],
  'mem_use_percent': [0.3616714477539063, 0.32275390625, 0.32275390625],
  'mem_use_amount': [904675328.0, 806551552.0, 806551552.0],
  'file_write_rate': [0.0, 0.0, 0.0],
  'file_read_rate': [0.0, 0.0, 0.0],
  'net_send_rate': [16767.496558054154,
   29167.369974103156,
   29167.369974103156],
  'net_recieve_rate': [10648.726480036716,
   18328.322482795626,
   18328.322482795626],
  'endtime': [1567084437323862.0, 1567084424174228.0, 1567084380682725.0],
  's_t': ['ts-order-service->ts-order-service',
   'ts-station-service->ts-station-service',
   'ts-order-service->ts-station-service'],
  'label': 0},
 {'trace_id': '00340510346cd70a0ccc9d66eeff4443',
  'timestamp': [1567084446055824.0],
  'latency': [2760.

# 绘制调用链

In [12]:
timestamp2string(1567084679)

'2019-08-29 21:17:59.000000'